In [1]:
import pandas as pd
from src.utils.helpers import *
import pickle
import glob

In [2]:
df = pd.read_csv("data/preprocessed/cleaned_merged_movies.csv")

output_4o = []

output_files = sorted(glob.glob('data/promptengineering/output_*.txt'), key=lambda x: int(x.split('_')[1].split('.txt')[0]))

# read all the output files
for file in output_files:
    with open(file, 'r') as f:
        output_4o.append(f.read())
        
output_4o

['Western  \nJoe Collins, American bank security consultant, values cunning, heroism, cleverness, Antihero  \nSarge, corrupt U.S. Army sergeant, values ruthlessness, violence, power, Antihero  \nCunning, heroism, cleverness, survival, Antiheroism  \nRuthlessness, violence, greed, betrayal, Antiheroism  \nHeist, crime, betrayal, survival, tension',
 "Western  \nJohnny Liston, justice, redemption, hero  \nSartana, tyranny, betrayal, antagonist  \nJustice, redemption, individualism, personal truth  \nTyranny, fear, betrayal, oppression  \nRevenge, self-discovery, moral conflict, hero's journey",
 'None  \nNone  \nNone  \nNone  \nNone  \nBetrayal, Greed, Bounty Hunter, Heist',
 'None  \nNone  \nNone  \nNone  \nNone  \nWestern, Frontier, Stranger, Rivalry, Money',
 'None  \nNone  \nNone  \nNone  \nNone  \nGay rights, counterculture, family conflict, protest, political history  ',
 'None  \nNone  \nNone  \nNone  \nNone  \nhorror, murder mystery, supernatural elements, societal struggles  ',


In [3]:
# save the output to a pickle file
pickle.dump(output_4o, open("data/preprocessed/output4o.pkl", "wb"))

In [4]:
parsed_4o = []

def parse_gpt_answer(answer):

    def split(line):
        line = re.sub(r"^[^:]*:", "", line)
        line = line.replace(", ", ",")
        # remove lasst character if " "
        if line[-1] == " ":
            line = line[:-1]
        return re.split(r",|\n", line)

    parsed_answer = {}
    
    answer = answer.replace(" \n", "\n")
    answer = answer.replace("\n\n", "\n")
    
    # Split the answer
    answer = answer.split("\n")
    
    print(answer)
    
    try:
        # Parse the Cold War side
        parsed_answer["cold_war_side"] = answer[0]
        # Parse the Western bloc representation
        parsed_answer["character_western_bloc_representation"] = split(answer[1])
        # Parse the Eastern bloc representation
        parsed_answer["character_eastern_bloc_representation"] = split(answer[2])
        # Parse the Western bloc values;
        parsed_answer["western_bloc_values"] = split(answer[3])
        # Parse the Eastern bloc values
        parsed_answer["eastern_bloc values"] = split(answer[4])
        # Parse the theme of the movie
        parsed_answer["theme"] = split(answer[5])
    except:
        parsed_answer = {"cold_war_side": 'None', "character_western_bloc_representation": 'None', "character_eastern_bloc_representation": 'None', "western_bloc_values": 'None', "eastern_bloc values": 'None', "theme": 'None'}

    return parsed_answer

output_4o = pickle.load(open("data/preprocessed/output4o.pkl", "rb"))

for answer in output_4o:
    parsed_4o.append(parse_gpt_answer(answer))

parsed_4o

['Western ', 'Joe Collins, American bank security consultant, values cunning, heroism, cleverness, Antihero ', 'Sarge, corrupt U.S. Army sergeant, values ruthlessness, violence, power, Antihero ', 'Cunning, heroism, cleverness, survival, Antiheroism ', 'Ruthlessness, violence, greed, betrayal, Antiheroism ', 'Heist, crime, betrayal, survival, tension']
['Western ', 'Johnny Liston, justice, redemption, hero ', 'Sartana, tyranny, betrayal, antagonist ', 'Justice, redemption, individualism, personal truth ', 'Tyranny, fear, betrayal, oppression ', "Revenge, self-discovery, moral conflict, hero's journey"]
['None ', 'None ', 'None ', 'None ', 'None ', 'Betrayal, Greed, Bounty Hunter, Heist']
['None ', 'None ', 'None ', 'None ', 'None ', 'Western, Frontier, Stranger, Rivalry, Money']
['None ', 'None ', 'None ', 'None ', 'None ', 'Gay rights, counterculture, family conflict, protest, political history  ']
['None ', 'None ', 'None ', 'None ', 'None ', 'horror, murder mystery, supernatural ele

[{'cold_war_side': 'Western ',
  'character_western_bloc_representation': ['Joe Collins',
   'American bank security consultant',
   'values cunning',
   'heroism',
   'cleverness',
   'Antihero'],
  'character_eastern_bloc_representation': ['Sarge',
   'corrupt U.S. Army sergeant',
   'values ruthlessness',
   'violence',
   'power',
   'Antihero'],
  'western_bloc_values': ['Cunning',
   'heroism',
   'cleverness',
   'survival',
   'Antiheroism'],
  'eastern_bloc values': ['Ruthlessness',
   'violence',
   'greed',
   'betrayal',
   'Antiheroism'],
  'theme': ['Heist', 'crime', 'betrayal', 'survival', 'tension']},
 {'cold_war_side': 'Western ',
  'character_western_bloc_representation': ['Johnny Liston',
   'justice',
   'redemption',
   'hero'],
  'character_eastern_bloc_representation': ['Sartana',
   'tyranny',
   'betrayal',
   'antagonist'],
  'western_bloc_values': ['Justice',
   'redemption',
   'individualism',
   'personal truth'],
  'eastern_bloc values': ['Tyranny', 'fear

In [5]:
movies_df = df.copy()
movies_df = movies_df.assign(**{key: [d[key] for d in parsed_4o] for key in parsed_4o[0].keys()})
movies_df

wikipedia_id freebase_id                            title  \
0         4213160.0   /m/0bq8q8                                $   
1               NaN         NaN              $1,000 on the Black   
2               NaN         NaN              $10,000 Blood Money   
3               NaN         NaN               $100,000 for Ringo   
4         2250713.0   /m/06z7m4                              '68   
...             ...         ...                              ...   
32434           NaN         NaN                    Убить дракона   
32435           NaN         NaN                  ’Round Midnight   
32436    12680019.0  /m/02x07kx                 …All the Marbles   
32437           NaN         NaN  …And the Fifth Horseman Is Fear   
32438     8277007.0  /m/026yqtg    …men Olsenbanden var ikke død   

                                languages  \
0                             ['English']   
1                 ['Deutsch', 'Italiano']   
2                                     NaN   
3                            ['Italiano']   
4                             ['English']   
...                                   ...   
32434                         ['Pусский']   
32435  ['English', 'Deutsch', 'Français']   
32436                         ['English']   
32437                           ['Český']   
32438                       ['Norwegian']   

                                     countries  \
0                 ['United States of America']   
1                         ['Italy', 'Germany']   
2                             ['Soviet Union']   
3                                    ['Italy']   
4      ['United States of America', 'Hungary']   
...                                        ...   
32434                    ['Russia', 'Germany']   
32435   ['France', 'United States of America']   
32436             ['United States of America']   
32437                       ['Czech Republic']   
32438                               ['Norway']   

                                                  genres  \
0      ['Drama', 'Comedy', 'Action', 'Thriller', 'Hei...   
1                                            ['Western']   
2                                   ['Drama', 'Western']   
3                                   ['Drama', 'Western']   
4      ['Drama', 'Coming of age', 'Family Drama', 'Pe...   
...                                                  ...   
32434                               ['Fantasy', 'Drama']   
32435                                          ['Drama']   
32436                ['Drama', 'Comedy', 'Comedy-drama']   
32437                                   ['Drama', 'War']   
32438                        ['Comedy', 'Crime Fiction']   

                                keywords release_date  runtime  \
0                                    NaN   1971-12-17    119.0   
1                                    NaN   1966-12-18    104.0   
2                                    NaN   1967-01-01      NaN   
3      ['spaghetti western', 'whipping']   1965-11-18     98.0   
4                                    NaN   1988-01-01     98.0   
...                                  ...          ...      ...   
32434                                NaN   1988-01-01    123.0   
32435   ['jazz', 'musical', 'biography']   1986-09-23    133.0   
32436                                NaN   1981-01-01    113.0   
32437                                NaN   1965-02-12    100.0   
32438                                NaN   1984-01-01     89.0   

                                            plot_summary  year_release_date  \
0      Set in Hamburg, West Germany, several criminal...               1971   
1      Johnny Liston has just been released from pris...               1966   
2      Hired by a Mexican landowner to rescue his dau...               1967   
3      A stranger rides into Rainbow Valley where he'...               1965   
4      The father escaped the Soviet invasion of Buda...               1988   
...                                                  ...    

In [6]:
# save data in a csv
movies_df.to_csv("data/preprocessed/v1_movies.csv", index=False)

In [ ]:
movies_df.load("data/preprocessed/v1_movies.csv")
movies_df["cold_war_side"].value_counts()

In [7]:
# exploration

subset_movies = ["High School Musical", "From Russia with Love", "The Godfather", "First Blood", "Oshibka rezidenta"]
subset_movies_df = movies_df[movies_df["title"].isin(subset_movies)]

subset_movies_df


wikipedia_id freebase_id                  title  \
8357       872441.0   /m/03kfz0            First Blood   
8887      6446071.0  /m/025twgt  From Russia with Love   
25205     2466773.0   /m/07g1sm          The Godfather   

                                               languages  \
8357                                         ['English']   
8887   ['Romani language', 'English', 'Türkçe', 'Pусс...   
25205  ['English', 'Sicilian', 'Italiano', 'Italian',...   

                          countries  \
8357   ['United States of America']   
8887             ['United Kingdom']   
25205  ['United States of America']   

                                                  genres  \
8357   ['Psychological thriller', 'Action Thrillers',...   
8887   ['Glamorized Spy Film', 'Thriller', 'Action', ...   
25205  ['Gangster Film', 'New Hollywood', 'Film adapt...   

                                                keywords release_date  \
8357   ['prison', 'vietnam veteran', 'falsely accused...   1982-10-22   
8887   ['venice', 'london england', 'terror', 'englan...   1963-10-11   
25205  ['italy', 'love at first sight', 'loss of fath...   1972-03-15   

       runtime                                       plot_summary  \
8357      93.0  John Rambo  is a former member of an elite Uni...   
8887     111.0  SPECTRE's expert planner Kronsteen devises a p...   
25205    177.0  On the day of his only daughter's wedding, Vit...   

       year_release_date cold_war_side  \
8357                1982      Western    
8887                1963      Western    
25205               1972         None    

                   character_western_bloc_representation  \
8357   [John Rambo, military honor, individualistic h...   
8887   [ heroism, wit, intelligence, archetype: the s...   
25205  [Michael Corleone, ambition, transformation, a...   

                   character_eastern_bloc_representation  \
8357   [Sheriff Will Teasle, law enforcement, authori...   
8887   [ loyalty, innocence, archetype: the unwitting...   
25205                                             [None]   

                                     western_bloc_values  \
8357                                              [None]   
8887   [ cunning, manipulation, archetype: the antago...   
25205  [Power, family loyalty, American Dream, corrup...   

                                     eastern_bloc values  \
8357            [Courage, honor, individualism, heroism]   
8887   [ bravery, resourcefulness, loyalty to his cou...   
25205                                             [None]   

                                                   theme  
8357   [Authority, oppression, misguided justice, com...  
8887   [ deception, cold-heartedness, betrayal, ruthl...  
25205  [Crime, power dynamics, family, betrayal, mora...